# Shoreline position v.s. wave energy
This notebook looks at the relationship between shoreline position and wave energy.

## Setup notebook

In [ ]:
import os
import datetime
import pickle
import fiona
import shapely
import matplotlib.pyplot as plt
import pandas as pd
import geopandas
from scipy.stats import percentileofscore
from shapely.geometry import Point
import numpy as np
import requests
from bs4 import BeautifulSoup
import urllib.parse
import itertools
from tqdm import tqdm
import glob
from scipy.interpolate import griddata, SmoothBivariateSpline
from scipy.ndimage.filters import gaussian_filter
import colorcet as cc

### Shoreline positions

In [ ]:
# Import Killian's data
shorelines = pickle.load(open("14_timeseries_Australia_2.pkl", "rb"))
beaches = fiona.open("14_beaches_Australia.geojson")
polygons = fiona.open("14_polygons_Australia.geojson")
transects = fiona.open("14_transects_Australia.geojson")

In [ ]:
def df_from_csv(csv, index_col, data_folder='../data/interim'):
    print('Importing {}'.format(csv))
    return pd.read_csv(os.path.join(data_folder,csv), index_col=index_col)

# Import Chris' data
df_sites = df_from_csv('sites.csv', index_col=[0])
df_obs_impacts = df_from_csv('impacts_observed.csv', index_col=[0])
df_waves = df_from_csv('waves.csv', index_col=[0,1])
df_waves.index = df_waves.index.set_levels([df_waves.index.levels[0], pd.to_datetime(df_waves.index.levels[1])])

In [ ]:
# Get coorindates of transects where Killian has given shoreline data
transect_data =  [x for x in transects if x['properties']['id'] in shorelines.keys()]
transect_dict = [{'name':x['properties']['name'],
                 'id':x['properties']['id'],
                 'orientation':x['properties']['orientation'],
                 'start_coords': Point(x['geometry']['coordinates'][0][0], x['geometry']['coordinates'][0][1]),
                 'end_coords': Point(x['geometry']['coordinates'][1][0], x['geometry']['coordinates'][1][1])} for x in transect_data]
df_transects = pd.DataFrame(transect_dict)
gdf_transects = geopandas.GeoDataFrame(df_transects, geometry='start_coords',crs={'init':'epsg:4326'})

# Find closest Chris transect to each one of Kilian's transects
# First transform coords using geopandas
df_sites['coords'] = list(zip(df_sites.lon, df_sites.lat))
df_sites['coords'] = df_sites['coords'].apply(Point)
gdf_sites = geopandas.GeoDataFrame(df_sites, geometry='coords',crs={'init':'epsg:4326'})
gdf_sites['site_id'] = gdf_sites.index

In [ ]:
# Find nearest Chris transect for each of Kilian's transect

from shapely.ops import nearest_points

def nearest(row,
            geom_union,
            df1,
            df2,
            geom1_col='geometry',
            geom2_col='geometry',
            src_column=None):
    """Find the nearest point and return the corresponding value from specified column."""
    # Find the geometry that is closest
    nearest = df2[geom2_col] == nearest_points(row[geom1_col], geom_union)[1]
    # Get the corresponding value from df2 (matching is based on the geometry)
    value = df2[nearest][src_column].get_values()[0]
    return value

unary_union = gdf_sites.unary_union
gdf_transects['chris_site_id'] = gdf_transects.apply(nearest,
                                                     geom_union=unary_union,
                                                     df1=gdf_transects,
                                                     df2=gdf_sites,
                                                     geom1_col='start_coords',
                                                     geom2_col='coords',
                                                     src_column='site_id',
                                                     axis=1)

In [ ]:
# Got the closests site_id, now check the distance. If distance too far between these sites, then probably not a good match.
gdf_transects = gdf_transects.merge(gdf_sites[['coords']], left_on='chris_site_id', right_on='site_id')
gdf_transects = gdf_transects.rename({'coords': 'chris_coords'},axis='columns')
gdf_transects
distances = gdf_transects[['start_coords']].to_crs(epsg=28356).distance(
    geopandas.GeoDataFrame(gdf_transects[['chris_coords']],
                           geometry='chris_coords',
                           crs={
                               'init': 'epsg:4326'
                           }).to_crs(epsg=28356))

gdf_transects['transect_to_chris_dist'] = distances

In [ ]:
# Limit used transects to 300 m max distance
gdf_transects = gdf_transects[gdf_transects.transect_to_chris_dist < 300]
gdf_transects

In [ ]:
# Calculate the change to the percentile of shoreline right after the storm
# Kilian's shorelines are given for z=0 MSL, so find change in shoreline due to storm
gdf_transects=gdf_transects.merge(df_obs_impacts.width_msl_change_m,left_on=['chris_site_id'], right_on=['site_id'])
gdf_transects

In [ ]:
# At each beach calculate percentile of shoreline right before the storm
data = []

for row in gdf_transects.iterrows():

    # Get shoreline records
    id_shorelines = shorelines[row[1].id]['chainage']
    id_dates = shorelines[row[1].id]['dates']

    # Find last date before June 2016 storm
    dt_storm = datetime.datetime(2016, 6, 3)
    dt_storm = dt_storm.replace(tzinfo=datetime.timezone.utc)
    mask = pd.Series([x < dt_storm for x in id_dates])
    i_last_obs = mask[::-1].idxmax()

    last_obs_ch = id_shorelines[i_last_obs]
    last_obs_date = id_dates[i_last_obs]
    post_storm_ch = last_obs_ch + row[1].width_msl_change_m

    prestorm_shoreline_pctile = percentileofscore(id_shorelines[~np.isnan(id_shorelines)], last_obs_ch)
    poststorm_shoreline_pctile = percentileofscore(id_shorelines[~np.isnan(id_shorelines)],
                                                   post_storm_ch)
    change_shoreline_pctile = poststorm_shoreline_pctile - prestorm_shoreline_pctile

    rel_change_shoreline_pctile = (poststorm_shoreline_pctile- prestorm_shoreline_pctile)/prestorm_shoreline_pctile *100
    
    # Calculate percentile of shoreline score
    data.append({
        'prestorm_shoreline_pctile': prestorm_shoreline_pctile,
        'poststorm_shoreline_pctile': poststorm_shoreline_pctile,
        'change_shoreline_pctile': change_shoreline_pctile,
        'rel_change_shoreline_pctile': rel_change_shoreline_pctile,
        'index': row[0]
    })

data = pd.DataFrame(data).set_index('index')
gdf_transects = gdf_transects.join(data)
gdf_transects

In [ ]:
# Grab data from NSW Nearshore wave transformation tool.
# Need to relate Kilian's site id
sites = [{
    'id': 'way4042355',
    'site_id': 'DEEWHYs0003',
    'nsw_nearshore_id': 1007832
}, {
    'id': 'way13858409',
    'site_id': 'DEEWHYn0003',
    'nsw_nearshore_id': 1007822,   
}, {
    'id': 'way13858412',
    'site_id': 'MONA0011',
    'nsw_nearshore_id': 1007726,   
},
{
    'id': 'way14040821',
    'site_id': 'NARRA0007',
    'nsw_nearshore_id': 1007760,   
},{
    'id': 'way14040977',
    'site_id': 'NARRA0018',
    'nsw_nearshore_id': 1007770,   
},{
    'id': 'way14041013',
    'site_id': 'NARRA0030',
    'nsw_nearshore_id': 1007778,   
},{
    'id': 'way25005079',
    'site_id': 'MACM0009',
    'nsw_nearshore_id': 1007354,   
},{
    'id': 'way54609773',
    'site_id': 'WAMBE0005',
    'nsw_nearshore_id': 1007264,   
},{
    'id': 'way54667480',
    'site_id': 'AVOCAn0005',
    'nsw_nearshore_id': 1007306,   
},{
    'id': 'way54669965',
    'site_id': 'AVOCAs0004',
    'nsw_nearshore_id': 1007312,   
},{
    'id': 'way134627391',
    'site_id': 'ONEMILE0007',
    'nsw_nearshore_id': 1005098,   
},{
    'id': 'way159040990',
    'site_id': 'LHOUSE0004',
    'nsw_nearshore_id': 1005448,   
},{
    'id': 'way173070325',
    'site_id': 'LHOUSEn0077',
    'nsw_nearshore_id': 1004186,   
},{
    'id': 'way182614828',
    'site_id': 'TREACH0009',
    'nsw_nearshore_id': 1005472,   
},{
    'id': 'way189407637',
    'site_id': 'NSHORE_n0063',
    'nsw_nearshore_id': 1003994,   
},{
    'id': 'way190929758',
    'site_id': 'CRESn0069',
    'nsw_nearshore_id': 1003708,   
},{
    'id': 'way222144734',
    'site_id': 'BLUEYS0002',
    'nsw_nearshore_id': 1005316,   
},{
    'id': 'way222145626',
    'site_id': 'BOOM0008',
    'nsw_nearshore_id': 1005298,   
},{
    'id': 'way224198013',
    'site_id': 'MANNING0048',
    'nsw_nearshore_id': 1004712,   
},{
    'id': 'way450323845',
    'site_id': 'NAMB0033',
    'nsw_nearshore_id': np.nan,   
},{
    'id': 'relation2303044',
    'site_id': 'ENTRA0041',
    'nsw_nearshore_id': 1007110,   
},{
    'id': 'relation2723197',
    'site_id': 'GRANTSn0022',
    'nsw_nearshore_id': 1004296,   
}
]

In [ ]:
def nearshore_wave_csv_url(id,start_date,end_date):
    URL = 'http://www.nswaves.com.au/transform.php'
    payload = {
        'init': '1',
        'type': 'Transform-Full',
        'startsite': '{}'.format(id),
        'endsite': '{}'.format(id),
        'timestep': 'null',
        'startdate': start_date.strftime('%Y-%m-%d'),
        'starthour': '00',
        'enddate': end_date.strftime('%Y-%m-%d'),
        'endhour': '00',
        'sitestep': '1',
        'method': 'Parametric',
        'source': 'Waverider',
        'filename': 'ckl',
        'format': 'csv',
    }

    session = requests.session()
    r = requests.post(URL, data=payload)
    
    soup = BeautifulSoup(r.text)
    
    # Check if data extraction was successful
    if soup.findAll(text="OK :  Data Extraction Successful - Click filename/s to download data file"):

        # Find all links
        for link in soup.find_all('a'):

            href = link.get('href')
            if '/data/full' not in href:
                continue

            # Convert to absolute convert to absolute url
            csv_url = urllib.parse.urljoin(URL, href)

            return csv_url
    else:
        return None

    
def download_csv(url, file_path):
    urllib.request.urlretrieve(url,file_path)
    print('Downloaded {}'.format(file_path))
    
    
def daterange(start_date, end_date,delta):
    while start_date < end_date:
        yield start_date
        start_date += delta
        
def download_nearshore_csv(id, site_id, nsw_nearshore_id, start_date, end_date,output_folder='./14_nearshore_waves/'):
    
    # Create output folder if doesn't already exists
    os.makedirs(output_folder, exist_ok=True)

    # Output filename
    output_filename = '{}_{}_{}_{}_{}.csv'.format(
    id,
        site_id,
        nsw_nearshore_id,
        start_date.strftime('%Y%m%d'),
        end_date.strftime('%Y%m%d'),
    )
    output_filepath = os.path.join(output_folder,output_filename)

    # Don't download if file already exists
    if os.path.isfile(output_filepath):
        return

    csv_url = nearshore_wave_csv_url(nsw_nearshore_id,start_date,end_date)

    if csv_url:
        download_csv(csv_url, output_filepath)
    else:
        print('No url found')

In [ ]:
# start_year = 2005
# end_year = 2015
# output_folder = './14_nearshore_waves/'

# # Create list of start end dates we want to request
# date_ranges = [(datetime.datetime(x, 1, 1), datetime.datetime(x, 12, 31))
#                for x in range(start_year, end_year + 1)]

# inputs = list(itertools.product(sites, date_ranges))

# for inpt in inputs:
#     download_nearshore_csv(inpt[0]['id'], inpt[0]['site_id'], inpt[0]['nsw_nearshore_id'], inpt[1][0], inpt[1][1])
#     break

In [ ]:
# # Use a queue to get data

# from queue import Queue
# from threading import Thread
# q = Queue(maxsize=0)
# num_theads = 4

# start_year = 2005
# end_year = 2015
# date_ranges = [(datetime.datetime(x, 1, 1), datetime.datetime(x, 12, 31))
#                for x in range(start_year, end_year + 1)]

# inputs = [x for x in list(itertools.product(sites, date_ranges))]

# #Populating Queue with tasks
# results = [{} for x in inputs]

# #load up the queue with the urls to fetch and the index for each job (as a tuple):
# for i, inpt in enumerate(inputs):
#     q.put((i, inpt))


# # Threaded function for queue processing.
# def crawl(q, result):
#     while not q.empty():
#         work = q.get()  #fetch new work from the Queue
#         print(work)
#         download_nearshore_csv(work[1][0]['id'], work[1][0]['site_id'],
#                                work[1][0]['nsw_nearshore_id'], work[1][1][0],
#                                work[1][1][1])
#         #signal to the queue that task has been processed
#         q.task_done()
#     return True


# #Starting worker threads on queue processing
# for i in range(num_theads):
#     print('Starting thread {}'.format(i))
#     worker = Thread(target=crawl, args=(q, results))
#     worker.setDaemon(True)  #setting threads as "daemon" allows main program to
#     #exit eventually even if these dont finish
#     #correctly.
#     worker.start()

# #now we wait until the queue has been processed
# q.join()
# print('All tasks completed.')

In [ ]:
# For each site, get
for site in sites:

    # print(site)
    df_sites

    # Get shoreline orientation
    orientation = df_sites.loc[[site['site_id']]].orientation.iloc[0]

    # Get peak hour wave energy from June 2016 storm
    max_hrly_wave_power = df_waves.loc[[site['site_id']]].Pxs.max()

    # Load nearshore wave csv files into one dataframe
    site_nearshore_wave_files = glob.glob('./14_nearshore_waves/*{}*'.format(
        site['site_id']))

    if len(site_nearshore_wave_files) == 0:
        continue

    df_hist_waves = pd.concat((pd.read_csv(f,
                                           skiprows=8,
                                           index_col=0,
                                           names=['Hs', 'Tp', 'dir'],
                                           na_values=' NaN')
                               for f in site_nearshore_wave_files))
    df_hist_waves.index = pd.to_datetime(df_hist_waves.index)

    # At each row, calculate crossshore component of nearshore wave energy
    df_hist_waves['d'] = 10
    df_hist_waves['L'] = 9.81 * df_hist_waves.Tp**2 / 2 / np.pi
    df_hist_waves['n'] = 0.5 * (
        1 + (4 * np.pi * df_hist_waves.d / df_hist_waves.L) /
        (np.sinh(4 * np.pi * df_hist_waves.d / df_hist_waves.L)))
    df_hist_waves['E'] = 1 / 16 * 1025 * 9.81 * df_hist_waves.Hs**2
    df_hist_waves['C'] = 9.81 * df_hist_waves.Tp / 2 / np.pi * np.tanh(
        2 * np.pi * df_hist_waves.d / df_hist_waves.L)
    df_hist_waves['shoreline_tn_angle'] = 270 - orientation
    df_hist_waves.loc[
        df_hist_waves.shoreline_tn_angle > 360,
        'shoreline_tn_angle'] = df_hist_waves.shoreline_tn_angle - 360
    df_hist_waves[
        'alpha'] = df_hist_waves.shoreline_tn_angle - df_hist_waves.dir
    df_hist_waves[
        'Px'] = df_hist_waves.n * df_hist_waves.E * df_hist_waves.C * np.cos(
            np.deg2rad(df_hist_waves.alpha))

    # Apply percentileofscore for June 2016 wave energy
    storm_Px_hrly_pctile = percentileofscore(df_hist_waves.Px.dropna().values,
                                             max_hrly_wave_power,
                                             kind='mean')

    # Calculate cumulate wave energy from storm
    idx = ((df_waves.index.get_level_values('datetime') > '2016-06-04') &
           (df_waves.index.get_level_values('datetime') < '2016-06-07') &
           (df_waves.index.get_level_values('site_id') == site['site_id']))
    hrs = len(df_waves[idx])
    Pxscum_storm = df_waves[idx].Pxs.sum()
    
    # Calculate cumulate wave energy of mean wave conditions over length of storm
    Pxscum_mean = df_hist_waves['Px'].mean() * hrs
    Pxscum_storm_mean_ratio = Pxscum_storm / Pxscum_mean

    # Add to gdf_transects dataframe
    idx = gdf_transects[gdf_transects.chris_site_id == site['site_id']].index
    gdf_transects.loc[idx, 'storm_Px_hrly_pctile'] = storm_Px_hrly_pctile
    gdf_transects.loc[idx, 'Pxscum_storm'] = Pxscum_storm
    gdf_transects.loc[idx, 'Pxscum_mean'] = Pxscum_mean
    gdf_transects.loc[idx, 'Pxscum_storm_mean_ratio'] = Pxscum_storm_mean_ratio


In [ ]:
gdf_transects.sort_values(by='Pxscum_storm_mean_ratio',ascending=False).head()

In [ ]:
gdf_transects.sort_values(by='rel_change_shoreline_pctile').head()

In [ ]:
# Drop nans
gdf_transects = gdf_transects.dropna(axis='index',
                                     subset=[
                                         'Pxscum_storm_mean_ratio',
                                         'prestorm_shoreline_pctile',
                                         'change_shoreline_pctile',
                                         'rel_change_shoreline_pctile'
                                     ],
                                     how='any')

# Grid results
grid_x, grid_y = np.mgrid[0:2:100j, 0:100:100j]

x_vals = gdf_transects.Pxscum_storm_mean_ratio.values
y_vals = gdf_transects.prestorm_shoreline_pctile.values
z_vals = gdf_transects.rel_change_shoreline_pctile.values

points = [[x, y] for x, y in zip(
    x_vals,
    y_vals,
)]

grid = griddata((x_vals,y_vals), z_vals, (grid_x, grid_y), method='cubic')

# Smooth data
# https://stackoverflow.com/a/34370291
# grid = gaussian_filter(grid, sigma=0.5)

In [ ]:
def round_down(num, divisor):
    return num - (num%divisor)

def round_up(x, divisor): 
    return (x + divisor - 1) // divisor * divisor

In [ ]:
gdf_transects[gdf_transects.prestorm_shoreline_pctile<40].sort_values(by='change_shoreline_pctile',ascending=True).head()

In [ ]:
# Plot peak wave energy pctile vs prestorm shoreline percentile vs change in shoreline percentile

x_col = 'Pxscum_storm_mean_ratio'
y_col = 'prestorm_shoreline_pctile'
# z_col = 'rel_change_shoreline_pctile'
z_col = 'change_shoreline_pctile'

# Drop nans
gdf_transects = gdf_transects.dropna(axis='index',
                                     subset=[x_col, y_col,z_col
                                     ],
                                     how='any')

# Grid results
grid_x, grid_y = np.mgrid[0:25:100j, 0:100:100j]

x_vals = gdf_transects[x_col].values
y_vals = gdf_transects[y_col].values
z_vals = gdf_transects[z_col].values

grid = griddata((x_vals,y_vals), z_vals, (grid_x, grid_y), method='linear',rescale=True)

# Smooth data
# https://stackoverflow.com/a/34370291
# grid = gaussian_filter(grid, sigma=0.5)


# # 2D Spline interpolation
# s = SmoothBivariateSpline(x_vals, y_vals,z_vals)
# spline_x = np.arange(1,25,0.1)
# spline_y = np.arange(0,100,0.5)
# spline_z = s(spline_x, spline_y,grid=True)
# spline_grid_x, spline_grid_y = np.meshgrid(spline_x, spline_y)


# Create figure
fig = plt.figure(figsize=(3, 3), dpi=150, facecolor='w', edgecolor='k')
ax = fig.add_subplot(111)

# Define colors
cmap_interval = 25
cmap = cc.cm.fire
vmin = round_down(np.min(z_vals), cmap_interval)
vmax = round_up(np.max(z_vals), cmap_interval)
levels = [x*cmap_interval for x in range(-4,2)]


# Plot SPLINE grid surface
# cf = ax.contourf(spline_grid_x, spline_grid_y, spline_z.T,levels=levels, cmap=cmap,vmin=vmin,vmax=vmax)

# Plot SPLINE contours
# cs = plt.contour(grid_x, grid_y,grid,levels=levels,linewidths=0.5,colors='white', vmin=vmin,vmax=vmax)
# ax.clabel(cs, inline=1, fontsize=4,  fmt='%1.0f%%')


# Plot CUBIC FIT grid surface
cf = plt.contourf(grid_x, grid_y,grid,levels=levels, cmap=cmap,vmin=vmin,vmax=vmax)

# Plot CUBIC FIT contours
cs = plt.contour(grid_x, grid_y,grid,levels=levels,linewidths=0.5,colors='white', vmin=vmin,vmax=vmax)
ax.clabel(cs, inline=1, fontsize=4,  fmt='%1.0f%%')


scatter = ax.scatter(
    x=x_vals,
    y=y_vals,
    c=z_vals,
    s=1,
    cmap=cmap,vmin=vmin,vmax=vmax
)

ax.set_xlim([1,25])

ax.set_xlabel(x_col)
ax.set_ylabel(y_col)

cbar = plt.colorbar(cf)
cbar.set_label(z_col)

ax.grid(True, linestyle="--", alpha=0.2, color='grey', linewidth=1)

plt.show()

fig.savefig('14_beach_state_vs_wave_energy_{}'.format(z_col),dpi=600,bbox_inches = "tight", pad_inches=0.01)